Project: /overview/_project.yaml
Book: /overview/_book.yaml

<link rel="stylesheet" href="/site-assets/css/style.css">

<!-- DO NOT EDIT! Automatically generated file. -->


{% comment %}
The source of truth file can be found [here]: http://google3/zz
{% endcomment %}

<div itemscope itemtype="http://developers.google.com/ReferenceObject">
<meta itemprop="name" content="编写自己的回调函数" />
<meta itemprop="path" content="Guide & Tutorials" />
<meta itemprop="property" content="tf.keras.Sequential"/>
<meta itemprop="property" content="tf.keras.callbacks.Callback"/>
<meta itemprop="property" content="tf.keras.datasets.mnist.load_data"/>
<meta itemprop="property" content="tf.keras.layers.Dense"/>
<meta itemprop="property" content="tf.keras.optimizers.experimental.RMSprop"/>
</div>

# 编写自己的回调函数

<table class="tfo-notebook-buttons" align="left">
  <td>     <a target="_blank" href="https://tensorflow.google.cn/guide/keras/custom_callback"><img src="https://tensorflow.google.cn/images/tf_logo_32px.png">在 TensorFlow.org 上查看</a> </td>
  <td><a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/keras/custom_callback.ipynb"><img src="https://tensorflow.google.cn/images/colab_logo_32px.png">在 Google Colab 中运行 </a></td>
  <td>     <a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/keras/custom_callback.ipynb"><img src="https://tensorflow.google.cn/images/GitHub-Mark-32px.png">在 GitHub 上查看源代码</a> </td>
  <td>     <a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/zh-cn/guide/keras/custom_callback.ipynb"><img src="https://tensorflow.google.cn/images/download_logo_32px.png">下载笔记本</a>   </td>
</table>

## 简介

回调是一种可以在训练、评估或推断过程中自定义 Keras 模型行为的强大工具。示例包括使用 TensorBoard 来呈现训练进度和结果的 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/callbacks/TensorBoard"><code>tf.keras.callbacks.TensorBoard</code></a>，以及用来在训练期间定期保存模型的 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/callbacks/ModelCheckpoint"><code>tf.keras.callbacks.ModelCheckpoint</code></a>。

在本指南中，您将了解什么是 Keras 回调函数，它可以做什么，以及如何构建自己的回调函数。我们提供了一些简单回调函数应用的演示，以帮助您入门。

## 设置

In [2]:
import tensorflow as tf
from tensorflow import keras

2022-12-14 21:31:04.833621: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:31:04.833724: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 21:31:04.833734: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


## Keras 回调函数概述

所有回调函数都将 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/callbacks/Callback"><code>keras.callbacks.Callback</code></a> 类作为子类，并重写在训练、测试和预测的各个阶段调用的一组方法。回调函数对于在训练期间了解模型的内部状态和统计信息十分有用。

您可以将回调函数的列表（作为关键字参数 `callbacks`）传递给以下模型方法：

- <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#fit"><code>keras.Model.fit()</code></a>
- <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#evaluate"><code>keras.Model.evaluate()</code></a>
- <a href="https://www.tensorflow.org/api_docs/python/tf/keras/Model#predict"><code>keras.Model.predict()</code></a>

## 回调函数方法概述

### 全局方法

#### `on_(train|test|predict)_begin(self, logs=None)`

在 `fit`/`evaluate`/`predict` 开始时调用。

#### `on_(train|test|predict)_end(self, logs=None)`

在 `fit`/`evaluate`/`predict` 结束时调用。

### Batch-level methods for training/testing/predicting

#### `on_(train|test|predict)_batch_begin(self, batch, logs=None)`

正好在训练/测试/预测期间处理批次之前调用。

#### `on_(train|test|predict)_batch_end(self, batch, logs=None)`

在训练/测试/预测批次结束时调用。在此方法中，`logs` 是包含指标结果的字典。

### 周期级方法（仅训练）

#### `on_epoch_begin(self, epoch, logs=None)`

在训练期间周期开始时调用。

#### `on_epoch_end(self, epoch, logs=None)`

在训练期间周期开始时调用。

## 基本示例

让我们来看一个具体的例子。首先，导入 Tensorflow 并定义一个简单的序列式 Keras 模型：

In [3]:
# Define the Keras model to add callbacks to
def get_model():
    model = keras.Sequential()
    model.add(keras.layers.Dense(1, input_dim=784))
    model.compile(
        optimizer=keras.optimizers.RMSprop(learning_rate=0.1),
        loss="mean_squared_error",
        metrics=["mean_absolute_error"],
    )
    return model


然后，从 Keras 数据集 API 加载 MNIST 数据进行训练和测试：

In [4]:
# Load example MNIST data and pre-process it
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data()
x_train = x_train.reshape(-1, 784).astype("float32") / 255.0
x_test = x_test.reshape(-1, 784).astype("float32") / 255.0

# Limit the data to 1000 samples
x_train = x_train[:1000]
y_train = y_train[:1000]
x_test = x_test[:1000]
y_test = y_test[:1000]

接下来，定义一个简单的自定义回调函数来记录以下内容：

- `fit`/`evaluate`/`predict` 开始和结束的时间
- 每个周期开始和结束的时间
- 每个训练批次开始和结束的时间
- 每个评估（测试）批次开始和结束的时间
- 每次推断（预测）批次开始和结束的时间

In [5]:
class CustomCallback(keras.callbacks.Callback):
    def on_train_begin(self, logs=None):
        keys = list(logs.keys())
        print("Starting training; got log keys: {}".format(keys))

    def on_train_end(self, logs=None):
        keys = list(logs.keys())
        print("Stop training; got log keys: {}".format(keys))

    def on_epoch_begin(self, epoch, logs=None):
        keys = list(logs.keys())
        print("Start epoch {} of training; got log keys: {}".format(epoch, keys))

    def on_epoch_end(self, epoch, logs=None):
        keys = list(logs.keys())
        print("End epoch {} of training; got log keys: {}".format(epoch, keys))

    def on_test_begin(self, logs=None):
        keys = list(logs.keys())
        print("Start testing; got log keys: {}".format(keys))

    def on_test_end(self, logs=None):
        keys = list(logs.keys())
        print("Stop testing; got log keys: {}".format(keys))

    def on_predict_begin(self, logs=None):
        keys = list(logs.keys())
        print("Start predicting; got log keys: {}".format(keys))

    def on_predict_end(self, logs=None):
        keys = list(logs.keys())
        print("Stop predicting; got log keys: {}".format(keys))

    def on_train_batch_begin(self, batch, logs=None):
        keys = list(logs.keys())
        print("...Training: start of batch {}; got log keys: {}".format(batch, keys))

    def on_train_batch_end(self, batch, logs=None):
        keys = list(logs.keys())
        print("...Training: end of batch {}; got log keys: {}".format(batch, keys))

    def on_test_batch_begin(self, batch, logs=None):
        keys = list(logs.keys())
        print("...Evaluating: start of batch {}; got log keys: {}".format(batch, keys))

    def on_test_batch_end(self, batch, logs=None):
        keys = list(logs.keys())
        print("...Evaluating: end of batch {}; got log keys: {}".format(batch, keys))

    def on_predict_batch_begin(self, batch, logs=None):
        keys = list(logs.keys())
        print("...Predicting: start of batch {}; got log keys: {}".format(batch, keys))

    def on_predict_batch_end(self, batch, logs=None):
        keys = list(logs.keys())
        print("...Predicting: end of batch {}; got log keys: {}".format(batch, keys))


我们来试一下：

In [6]:
model = get_model()
model.fit(
    x_train,
    y_train,
    batch_size=128,
    epochs=1,
    verbose=0,
    validation_split=0.5,
    callbacks=[CustomCallback()],
)

res = model.evaluate(
    x_test, y_test, batch_size=128, verbose=0, callbacks=[CustomCallback()]
)

res = model.predict(x_test, batch_size=128, callbacks=[CustomCallback()])

Starting training; got log keys: []
Start epoch 0 of training; got log keys: []
...Training: start of batch 0; got log keys: []


...Training: end of batch 0; got log keys: ['loss', 'mean_absolute_error']
...Training: start of batch 1; got log keys: []
...Training: end of batch 1; got log keys: ['loss', 'mean_absolute_error']
...Training: start of batch 2; got log keys: []
...Training: end of batch 2; got log keys: ['loss', 'mean_absolute_error']
...Training: start of batch 3; got log keys: []
...Training: end of batch 3; got log keys: ['loss', 'mean_absolute_error']
Start testing; got log keys: []
...Evaluating: start of batch 0; got log keys: []
...Evaluating: end of batch 0; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 1; got log keys: []
...Evaluating: end of batch 1; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 2; got log keys: []
...Evaluating: end of batch 2; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 3; got log keys: []
...Evaluating: end of batch 3; got log keys: ['loss', 'mean_absolute_error']
Stop testing; go

Start testing; got log keys: []
...Evaluating: start of batch 0; got log keys: []
...Evaluating: end of batch 0; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 1; got log keys: []
...Evaluating: end of batch 1; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 2; got log keys: []
...Evaluating: end of batch 2; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 3; got log keys: []
...Evaluating: end of batch 3; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 4; got log keys: []
...Evaluating: end of batch 4; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 5; got log keys: []
...Evaluating: end of batch 5; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 6; got log keys: []
...Evaluating: end of batch 6; got log keys: ['loss', 'mean_absolute_error']
...Evaluating: start of batch 7; got log keys: []
...Evaluating: end of batch 7

...Predicting: start of batch 1; got log keys: []
...Predicting: end of batch 1; got log keys: ['outputs']
...Predicting: start of batch 2; got log keys: []
...Predicting: end of batch 2; got log keys: ['outputs']
...Predicting: start of batch 3; got log keys: []
...Predicting: end of batch 3; got log keys: ['outputs']
...Predicting: start of batch 4; got log keys: []
...Predicting: end of batch 4; got log keys: ['outputs']
...Predicting: start of batch 5; got log keys: []
...Predicting: end of batch 5; got log keys: ['outputs']
...Predicting: start of batch 6; got log keys: []
...Predicting: end of batch 6; got log keys: ['outputs']
...Predicting: start of batch 7; got log keys: []
...Predicting: end of batch 7; got log keys: ['outputs']
Stop predicting; got log keys: []
8/8 [==============================] - 0s 2ms/step


### `logs` 字典的用法

`logs` 字典包含损失值，以及批次或周期结束时的所有指标。示例包括损失和平均绝对误差。

In [7]:
class LossAndErrorPrintingCallback(keras.callbacks.Callback):
    def on_train_batch_end(self, batch, logs=None):
        print(
            "Up to batch {}, the average loss is {:7.2f}.".format(batch, logs["loss"])
        )

    def on_test_batch_end(self, batch, logs=None):
        print(
            "Up to batch {}, the average loss is {:7.2f}.".format(batch, logs["loss"])
        )

    def on_epoch_end(self, epoch, logs=None):
        print(
            "The average loss for epoch {} is {:7.2f} "
            "and mean absolute error is {:7.2f}.".format(
                epoch, logs["loss"], logs["mean_absolute_error"]
            )
        )


model = get_model()
model.fit(
    x_train,
    y_train,
    batch_size=128,
    epochs=2,
    verbose=0,
    callbacks=[LossAndErrorPrintingCallback()],
)

res = model.evaluate(
    x_test,
    y_test,
    batch_size=128,
    verbose=0,
    callbacks=[LossAndErrorPrintingCallback()],
)

Up to batch 0, the average loss is   27.21.
Up to batch 1, the average loss is  466.18.
Up to batch 2, the average loss is  318.49.
Up to batch 3, the average loss is  241.05.
Up to batch 4, the average loss is  194.55.
Up to batch 5, the average loss is  163.34.
Up to batch 6, the average loss is  140.86.
Up to batch 7, the average loss is  126.65.
The average loss for epoch 0 is  126.65 and mean absolute error is    6.03.
Up to batch 0, the average loss is    5.05.
Up to batch 1, the average loss is    5.07.
Up to batch 2, the average loss is    4.93.
Up to batch 3, the average loss is    4.83.
Up to batch 4, the average loss is    4.80.
Up to batch 5, the average loss is    4.63.
Up to batch 6, the average loss is    4.60.
Up to batch 7, the average loss is    4.56.
The average loss for epoch 1 is    4.56 and mean absolute error is    1.72.
Up to batch 0, the average loss is    5.34.
Up to batch 1, the average loss is    4.68.
Up to batch 2, the average loss is    4.76.
Up to batch 

## `self.model` 属性的用法

除了在调用其中一种方法时接收日志信息外，回调还可以访问与当前一轮训练/评估/推断有关的模型：`self.model`。

以下是您可以在回调函数中使用 `self.model` 进行的一些操作：

- 设置 `self.model.stop_training = True` 以立即中断训练。
- 转变优化器（可作为 `self.model.optimizer`）的超参数，例如 `self.model.optimizer.learning_rate`。
- 定期保存模型。
- 在每个周期结束时，在少量测试样本上记录 `model.predict()` 的输出，以用作训练期间的健全性检查。
- 在每个周期结束时提取中间特征的可视化，随时间推移监视模型当前的学习内容。
- 其他

下面我们通过几个示例来看看它是如何工作的。

## Keras 回调函数应用示例

### 在达到最小损失时尽早停止

第一个示例展示了如何通过设置 `self.model.stop_training`（布尔）属性来创建能够在达到最小损失时停止训练的 `Callback`。您还可以提供参数 `patience` 来指定在达到局部最小值后应该等待多少个周期然后停止。

<a href="https://www.tensorflow.org/api_docs/python/tf/keras/callbacks/EarlyStopping"><code>tf.keras.callbacks.EarlyStopping</code></a> 提供了一种更完整、更通用的实现。

In [8]:
import numpy as np


class EarlyStoppingAtMinLoss(keras.callbacks.Callback):
    """Stop training when the loss is at its min, i.e. the loss stops decreasing.

  Arguments:
      patience: Number of epochs to wait after min has been hit. After this
      number of no improvement, training stops.
  """

    def __init__(self, patience=0):
        super(EarlyStoppingAtMinLoss, self).__init__()
        self.patience = patience
        # best_weights to store the weights at which the minimum loss occurs.
        self.best_weights = None

    def on_train_begin(self, logs=None):
        # The number of epoch it has waited when loss is no longer minimum.
        self.wait = 0
        # The epoch the training stops at.
        self.stopped_epoch = 0
        # Initialize the best as infinity.
        self.best = np.inf

    def on_epoch_end(self, epoch, logs=None):
        current = logs.get("loss")
        if np.less(current, self.best):
            self.best = current
            self.wait = 0
            # Record the best weights if current results is better (less).
            self.best_weights = self.model.get_weights()
        else:
            self.wait += 1
            if self.wait >= self.patience:
                self.stopped_epoch = epoch
                self.model.stop_training = True
                print("Restoring model weights from the end of the best epoch.")
                self.model.set_weights(self.best_weights)

    def on_train_end(self, logs=None):
        if self.stopped_epoch > 0:
            print("Epoch %05d: early stopping" % (self.stopped_epoch + 1))


model = get_model()
model.fit(
    x_train,
    y_train,
    batch_size=64,
    steps_per_epoch=5,
    epochs=30,
    verbose=0,
    callbacks=[LossAndErrorPrintingCallback(), EarlyStoppingAtMinLoss()],
)

Up to batch 0, the average loss is   38.42.
Up to batch 1, the average loss is  423.00.
Up to batch 2, the average loss is  291.01.
Up to batch 3, the average loss is  221.08.
Up to batch 4, the average loss is  178.11.
The average loss for epoch 0 is  178.11 and mean absolute error is    8.10.
Up to batch 0, the average loss is    7.39.
Up to batch 1, the average loss is    6.79.
Up to batch 2, the average loss is    6.09.
Up to batch 3, the average loss is    5.66.
Up to batch 4, the average loss is    5.41.
The average loss for epoch 1 is    5.41 and mean absolute error is    1.89.
Up to batch 0, the average loss is    5.52.
Up to batch 1, the average loss is    5.45.
Up to batch 2, the average loss is    5.09.
Up to batch 3, the average loss is    5.00.
Up to batch 4, the average loss is    4.78.
The average loss for epoch 2 is    4.78 and mean absolute error is    1.81.
Up to batch 0, the average loss is    4.05.
Up to batch 1, the average loss is    4.77.
Up to batch 2, the avera

### 学习率规划

在此示例中，我们展示了如何在学习过程中使用自定义回调来动态更改优化器的学习率。

有关更通用的实现，请查看 <a href="https://www.tensorflow.org/api_docs/python/tf/keras/callbacks/LearningRateScheduler"><code>callbacks.LearningRateScheduler</code></a>。

In [9]:
class CustomLearningRateScheduler(keras.callbacks.Callback):
    """Learning rate scheduler which sets the learning rate according to schedule.

  Arguments:
      schedule: a function that takes an epoch index
          (integer, indexed from 0) and current learning rate
          as inputs and returns a new learning rate as output (float).
  """

    def __init__(self, schedule):
        super(CustomLearningRateScheduler, self).__init__()
        self.schedule = schedule

    def on_epoch_begin(self, epoch, logs=None):
        if not hasattr(self.model.optimizer, "lr"):
            raise ValueError('Optimizer must have a "lr" attribute.')
        # Get the current learning rate from model's optimizer.
        lr = float(tf.keras.backend.get_value(self.model.optimizer.learning_rate))
        # Call schedule function to get the scheduled learning rate.
        scheduled_lr = self.schedule(epoch, lr)
        # Set the value back to the optimizer before this epoch starts
        tf.keras.backend.set_value(self.model.optimizer.lr, scheduled_lr)
        print("\nEpoch %05d: Learning rate is %6.4f." % (epoch, scheduled_lr))


LR_SCHEDULE = [
    # (epoch to start, learning rate) tuples
    (3, 0.05),
    (6, 0.01),
    (9, 0.005),
    (12, 0.001),
]


def lr_schedule(epoch, lr):
    """Helper function to retrieve the scheduled learning rate based on epoch."""
    if epoch < LR_SCHEDULE[0][0] or epoch > LR_SCHEDULE[-1][0]:
        return lr
    for i in range(len(LR_SCHEDULE)):
        if epoch == LR_SCHEDULE[i][0]:
            return LR_SCHEDULE[i][1]
    return lr


model = get_model()
model.fit(
    x_train,
    y_train,
    batch_size=64,
    steps_per_epoch=5,
    epochs=15,
    verbose=0,
    callbacks=[
        LossAndErrorPrintingCallback(),
        CustomLearningRateScheduler(lr_schedule),
    ],
)


Epoch 00000: Learning rate is 0.1000.


Up to batch 0, the average loss is   36.36.
Up to batch 1, the average loss is  439.60.
Up to batch 2, the average loss is  300.96.
Up to batch 3, the average loss is  228.48.
Up to batch 4, the average loss is  183.92.
The average loss for epoch 0 is  183.92 and mean absolute error is    8.28.

Epoch 00001: Learning rate is 0.1000.
Up to batch 0, the average loss is    7.20.
Up to batch 1, the average loss is    6.45.
Up to batch 2, the average loss is    6.70.
Up to batch 3, the average loss is    6.50.
Up to batch 4, the average loss is    6.08.
The average loss for epoch 1 is    6.08 and mean absolute error is    2.05.

Epoch 00002: Learning rate is 0.1000.
Up to batch 0, the average loss is    5.59.
Up to batch 1, the average loss is    5.29.
Up to batch 2, the average loss is    4.82.
Up to batch 3, the average loss is    4.43.
Up to batch 4, the average loss is    4.36.
The average loss for epoch 2 is    4.36 and mean absolute error is    1.66.

Epoch 00003: Learning rate is 0.0

### 内置 Keras 回调函数

请务必阅读 [API 文档](https://tensorflow.google.cn/api_docs/python/tf/keras/callbacks/)查看现有的 Keras 回调函数。应用包括记录到 CSV、保存模型、在 TensorBoard 中可视化指标等等！